In [1]:
# from IPython.core.interactiveshell import InteractiveShell
# InteractiveShell.ast_node_interactivity = "all"

In [18]:
import csv
import time
import datetime
import pandas as pd
import os
import random
from Bio import SeqIO
import re
import copy
from multiprocessing import Process, Queue, Pool
from scipy.stats import hypergeom
import subprocess
from statsmodels.sandbox.stats.multicomp import multipletests

def virusrecom_analysis(x,viusrecom_identified,identidied_recom_info,virusrecom_output,virus_recom_code_path):
    num = x+1
    virusrecom_temp_fasta = virusrecom_output+"seq"+str(num)+"/"+"recom_parent_seq"+str(num)+".fasta"
    virusrecom_temp_output = virusrecom_output+"seq"+str(num)+"/"
    subprocess.call (["cd %s && \
        ../../main/virusrecom -a %s -q hCoV-19 -l %s -g n -m p -w 100 -s 20 -o %s" % (virus_recom_code_path,virusrecom_temp_fasta, virusrecom_output+"reference_lineages_name.txt",virusrecom_temp_output)],shell=True)
    with open(virusrecom_temp_output+"Possible_recombination_event_conciseness.txt") as f:
        rows = f.readlines()
    if rows[0].startswith("Possible major parent:"):
        PA = rows[0].strip().split("Possible major parent:")[1].strip().split("(gl")[0]
        PB = rows[3].split("\t")[0].strip()
        viusrecom_identified += 1
        with open(virusrecom_temp_fasta) as h:
            epi = h.readlines()[0].strip().split(">")[1]
            identidied_recom_info[epi] = [PA,PB]
    return  viusrecom_identified, identidied_recom_info


def recombination_detection_test(starttime,max_bk_num,Strain_list_snp,len_UAB,linA_list,samples_variants_all,feature_mutations,Lineage_v,mutaions_num,recom_total_num):
    import copy
    linA_list_deep = copy.deepcopy(linA_list)
    
    identidied_recom_info = {}
    for epi in Strain_list_snp:
        epi_record = {}
        epiV = samples_variants_all[epi]
        epi_feat = len(set(epiV) & set(feature_mutations))

        ### P-value for Non-recombination
        for lin_A in linA_list_deep:
            all_AA = len(Lineage_v[lin_A])
            all_AA_epi = len(set(Lineage_v[lin_A]) & set(epiV))
            pVal = hypergeom.sf(all_AA_epi-1,mutaions_num,all_AA,epi_feat)
            epi_record[str(lin_A)+"_"+str(lin_A)] = pVal
        # the least p-value for the Non-recombinant
        min_AA = min(epi_record, key = epi_record.get)

        ### P-value for Recombinant (A+B/A+B+A)
        A_already = []
        for A in linA_list_deep:
            A_already.append(A)
            A_epi = set(Lineage_v[A]) & set(epiV)
            if len(A_epi) < len_UAB:
                continue
            else:
                afterA_linB = set(linA_list_deep) - set(A_already)
                for B in afterA_linB:
                    B_epi = set(Lineage_v[B]) & set(epiV)
                    
                    if len(B_epi) < len_UAB:
                        continue
                    else:
                        unique_A = A_epi - B_epi
                        unique_B = B_epi - A_epi
                        union_AB_set = set(Lineage_v[A]) ^ set(Lineage_v[B])
                        AB_epi = sort_humanly(list(union_AB_set & set(epiV)))
                        recom_pattern = obtain_pattern(AB_epi, unique_A, unique_B)
                        # if (must_inA not in recom_pattern) or (must_inB not in recom_pattern):
                        if len(recom_pattern) <= 1:
                            continue
                        else:
                            change = bk_count(recom_pattern)
                            if change > max_bk_num:
                                continue
                            else:
                                all_AB = len(set(Lineage_v[A]) | set(Lineage_v[B]))  # K：正在分析的谱系对（如X+Y），其特征突变嵌合在基因组上的突变个数，对于X+Y，特征突变去重后的个数。 #去重
                                all_AB_epi = len(set(set(Lineage_v[A]) | set(Lineage_v[B])) & set(epiV)) # k：样本突变个数与正在分析的谱系对（如X+Y）特征突变集和的交集个数
                                pVal = hypergeom.sf(all_AB_epi - 1, mutaions_num, all_AB, epi_feat)
                                epi_record[str(A) + "_" + str(B)] =  pVal

        raw_pvals = list(epi_record.values())
        rejected, p_adjusted, _, alpha_corrected = multipletests(raw_pvals, alpha=0.05, method='bonferroni', is_sorted=False, returnsorted=False)
    
        lin_adjP = {}
        for p in range(len(p_adjusted)):
            lin_pair = list(epi_record.keys())[p]
            lin_adjP[lin_pair] = p_adjusted[p]
            
        min_adjp_pair = min(lin_adjP, key = lin_adjP.get)
        if min_adjp_pair == min_AA or lin_adjP[min_adjp_pair] >= 0.05: # 校正后p值显著，且排名top1，且其p值比PminAA小
            continue
        else:
            epiV = sort_humanly(epiV)
            lin_A_draw, lin_B_draw = min_adjp_pair.split("_")[0],min_adjp_pair.split("_")[1]
            lin_record, UA_mutate_unique, UB_mutate_unique, shared_mut, denovo_mut = calcul_bk(lin_A_draw, lin_B_draw, Lineage_v, epiV)
            if set(UA_mutate_unique + UB_mutate_unique) - set(Lineage_v[min_AA.split("_")[0]]) == set():
                continue
            else:
                if "Y"*len_UAB in lin_record and "X"*len_UAB in lin_record:
                    result_recom = [str(min_adjp_pair.split("_")[0]), str(min_adjp_pair.split("_")[1])]
                    identidied_recom_info[epi] = result_recom
    
    endtime = datetime.datetime.now()
    time_microsecond = (endtime - starttime).seconds * 1000 + (endtime - starttime).microseconds / 1000
    time_second, time_minute, time_hour = TimeConverter(time_microsecond)
    
    return identidied_recom_info, time_microsecond, time_second, time_minute, time_hour
        

###sort the feature SNP by genome location    
def sort_humanly(v_list): 
    def tryint(s):                       
        try:
            return int(s)
        except ValueError:
            return s

    def str2int(v_str):
        return [tryint(sub_str) for sub_str in re.split('([0-9]+)', v_str)]

    return sorted(v_list, key=str2int,reverse=False)


def obtain_pattern(AB_epi, unique_A, unique_B):
    recom_pattern = ""
    for v in AB_epi:
        if v in unique_A:
            recom_pattern = recom_pattern + "X"
        elif v in unique_B:
            recom_pattern = recom_pattern + "Y"

    return recom_pattern


def bk_count(recom_pattern):
    start = recom_pattern[0]
    change = 0
    for R in recom_pattern:
        if R != start:
            change += 1
            start = R

    return change


def calcul_bk(lin_A_draw, lin_B_draw, Lineage_v, epiV):
    feature_SNPA = Lineage_v[lin_A_draw]
    feature_SNPB = Lineage_v[lin_B_draw]
    A_B_shared = set(feature_SNPA) & set(feature_SNPB)
    UA_mutate = (set(feature_SNPA) & set(epiV)) - set(A_B_shared)
    UB_mutate = (set(feature_SNPB) & set(epiV)) - set(A_B_shared)
    sample_special = set(epiV) - (set(feature_SNPA) | set(feature_SNPB))

    UA_mutate_unique = []
    UB_mutate_unique = []
    shared_mut = []
    denovo_mut = []

    lin_record = ""
    for j in epiV:
        if j in A_B_shared:
            shared_mut.append(j)
        elif j in UA_mutate:
            UA_mutate_unique.append(j)
            lin_record = lin_record + "X"
        elif j in UB_mutate:
            UB_mutate_unique.append(j)
            lin_record = lin_record + "Y"
        elif j in sample_special:
            denovo_mut.append(j)

    return lin_record, UA_mutate_unique, UB_mutate_unique, shared_mut, denovo_mut


def TimeConverter(ms):
    s = round(ms / 1000, 2)
    m = round(s / 60, 2)
    h = round(m / 60, 2)
    return s, m, h


def creat_dir(turns_file):
    import os
    if not os.path.exists(turns_file):
        os.makedirs(turns_file)
        
                
def get_snps(sequence, ref_genome):
    snps = []
    gaps = []
    for gsite in range(0, len(ref_genome)):
        if sequence[gsite] != ref_genome[gsite] and sequence[gsite] in ['A', 'T', 'G', 'C']:
            snps.append(str(gsite+1)+'_'+sequence[gsite])
        elif sequence[gsite] == '-':
            gaps.append(gsite+1)
        
    continuous_gaps = []
    for gap in gaps:
        if len(continuous_gaps) == 0 or gap == continuous_gaps[-1]+1:
            continuous_gaps.append(gap)
        else:
            if len(continuous_gaps) % 3 == 0 and continuous_gaps[0] != 1 and continuous_gaps[-1] != 29891:
                snps.append(str(continuous_gaps[0])+'_'+'-'*len(continuous_gaps))
            continuous_gaps = [gap]

    return snps


def extract_ref_mut(sequence, ref_genome, lin_all_mutate):
    snps = get_snps(sequence, ref_genome)
    lin_all_mutate.extend(snps)
    return lin_all_mutate


In [5]:
### Extract the real sequences from recombination lineage with different sample size.
dirpath = "/home/jovyan/work/"
os.chdir(dirpath)

In [6]:
## read the meta file
meta_path = os.path.join("/home/jovyan/work/", '0_raw_data', 'metadata.tsv')
length = 27000
with open(meta_path, "r") as f:
    next(f)
    rows = f.readlines()

pango_lineage = {}
for i in rows:
    info = i.split("\t")
    seq_length = int(info[8])
    host = info[9]
    if host == "Human" and seq_length >= length and re.search('20\d\d-\d\d-\d\d', info[5]):
        epi = info[0]
        pango_lineage[epi] = info[13]

In [7]:
del rows

In [8]:
## the reference genome
with open(dirpath+"0_raw_data/EPI_ISL_402125.fasta", "r") as f:
    for record in SeqIO.parse(f, "fasta"):
        ID_name = str(record.id)
        seq = str(record.seq)
        ref_genome = str.upper(seq)

In [9]:
## read each sample's mutations
variants_all = {}
with open(os.path.join("/home/jovyan/work/", '0_raw_data',"snp_norm.txt"), "r") as f:
    for i in f.readlines():
        i_2 = i.split(':')
        variants_all[i_2[0]] = i_2[1].strip().split(',') 

In [10]:
# record samples for each recombinant lineages
recom_lin_epi = {}
for epi in pango_lineage:
    if pango_lineage[epi].startswith("X"):
        if pango_lineage[epi] not in recom_lin_epi:
            recom_lin_epi[pango_lineage[epi]] = [epi]
        else:
            recom_lin_epi[pango_lineage[epi]].append(epi)

candilist = set(recom_lin_epi.keys())

In [11]:
parents = {}
with open(dirpath+"0_raw_data/parents.txt") as f:
    for i in f.readlines():
        parents[i.strip().split(":")[0]] = i.strip().split(":")[1].split(",")

In [12]:
all_need_parents = []
all_need_parents = []
need_recom = []
for lin in candilist:
    if lin in parents:
        all_need_parents.extend(parents[lin])
        need_recom.append(lin)
    elif len(lin)>3:
        parents[lin] =  parents[lin[:3]]
        all_need_parents.extend(parents[lin])
        need_recom.append(lin)
need_recom = set(need_recom)

In [19]:
len(need_recom & set(parents.keys())) == len(need_recom)

True

In [20]:
recom_epi = []
for epi in pango_lineage:
    if pango_lineage[epi] in need_recom:
        recom_epi.append(epi)

In [21]:
print(len(set(all_need_parents)))
all_need_parents= set(all_need_parents) 

29


In [22]:
parents_lin_epi = {}
for lin in  all_need_parents:
    parents_lin_epi[lin] = [epi for epi in pango_lineage if pango_lineage[epi] == lin]

In [23]:
len(parents_lin_epi)

29

In [27]:
for n in [0,1,2,3,4]:
    rn,pn = 1, 10
    parents_total_epi = []
    for lin in parents_lin_epi:
        parents_total_epi.extend(random.sample(parents_lin_epi[lin], pn))

    all_parents_seq = {}
    num = 0
    for epi in parents_total_epi:
        num+=1
        name_off = pango_lineage[epi]+"_ID"+str(num)
        mut_site = []
        for site in variants_all[epi]:
            mut_site.append(int(site.split("_")[0]))
        epi_seq = ""
        jump = 0
        need_jump = 0
        for pos in range(len(ref_genome)):
            if jump == need_jump:
                if pos+1 in mut_site:
                    for i in variants_all[epi]:
                        if str(pos+1) == str(i.split('_')[0]) and "---" not in i:
                            letter = i.split('_')[1]
                            epi_seq += letter
                        elif str(pos+1) == str(i.split('_')[0]) and "---" in i:
                            need_jump = len(i.split('_')[1]) -1
                            letter = i.split('_')[1]
                            epi_seq += letter
                else:
                    epi_seq += ref_genome[pos]
            else:
                need_jump = need_jump -1
                continue
        if len(epi_seq) != 29903:
            less_epi = random.sample(parents_lin_epi[pango_lineage[epi]], 1)
            parents_total_epi.extend(less_epi)
            continue
        else:
            all_parents_seq[name_off] = epi_seq
    
    turns_path = dirpath+"2_first_test/turns"+str(n+1)+"/"
    parent_fasta_file = turns_path+"real_parental_lineage_"+str(len(all_parents_seq))+".fasta"
    with open(parent_fasta_file,"w+") as f:
        for epi in all_parents_seq:
            try:
                f.write(">"+epi+"\n")
                f.write(all_parents_seq[epi]+"\n")
            except:
                continue

    import random
    less_num = 0
    total_epi = []
    for lin in need_recom:
        epi_len = len(recom_lin_epi[lin])
        if epi_len < rn:
            total_epi.extend(random.sample(recom_lin_epi[lin], epi_len))
            less_num += rn - epi_len
        else:
            total_epi.extend(random.sample(recom_lin_epi[lin], rn))
            
    less_epi = random.sample(recom_epi, less_num)
    total_epi.extend(less_epi)


    total_epi_uni = set(total_epi)
    all_epi_seq = {}
    for epi in total_epi:
        if epi not in all_epi_seq:
            mut_site = []
            for site in variants_all[epi]:
                mut_site.append(int(site.split("_")[0]))
                
            epi_seq = ""
            jump = 0
            need_jump = 0
            for pos in range(len(ref_genome)):
                if jump == need_jump:
                    if pos+1 in mut_site:
                        for i in variants_all[epi]:
                            if str(pos+1) == str(i.split('_')[0]) and "---" not in i:
                                letter = i.split('_')[1]
                                epi_seq += letter
                            elif str(pos+1) == str(i.split('_')[0]) and "---" in i:
                                need_jump = len(i.split('_')[1]) -1
                                letter = i.split('_')[1]
                                epi_seq += letter
                    else:
                        epi_seq += ref_genome[pos]
                else:
                    need_jump = need_jump -1
                    continue
            if len(epi_seq) != 29903: # '27792_--',recom_epi
                total_epi.extend(random.sample(recom_epi, 1))
                continue
            else:
                all_epi_seq[epi] = epi_seq
                
    recom_total_num = sample_size=  len(all_epi_seq)
    child_fasta_file = turns_path+"real_recom_lineage_samples_"+str(sample_size)+".fasta"
    with open(child_fasta_file,"w+") as f:
        for epi in all_epi_seq:
            f.write(">"+epi+"\n")
            f.write(all_epi_seq[epi]+"\n")

    with open(turns_path+"methods_results_0605.csv","a+")as h:
        h.write(",".join(["turns","method","sample_size","tpr","time_microsecond","time_second","time_minute","time_hour","core"])+"\n")

    with open(turns_path+"methods_accurate_0605.csv","a+")as h:
        h.write(",".join(["turns","method","accurate_rate"])+"\n")
    
    from multiprocessing import Process, Queue, Pool, Manager
    import subprocess
    cor_num = 1 # Number of processes to create
    
    ### ---------------------------- Test different recombination detection methods ----------------------------------
    #### -----------------------------   CovRecomb   -----------------------------
    turns_path = dirpath+"2_first_test/turns"+str(n+1)+"/"
    for file in os.listdir(turns_path):
        if file.startswith("real_parental_lineage_"):
            parent_fasta_file = turns_path+file
        elif file.startswith("real_recom_lineage_samples_"):
            child_fasta_file = turns_path+file
    ## CovRecomb
    import datetime
    starttime = datetime.datetime.now()
    # read sequences
    seq_parents = {}
    for seq_record in SeqIO.parse(parent_fasta_file, "fasta"):
        seq_parents[seq_record.id] = str(seq_record.seq)

    # Extract feature mutations
    Lineage_v = {}
    for lin in all_need_parents:
        lin_all_mutate = [] # Record all the mutations within each lineage
        count_target_lin = 0 # Record the number of samples within each lineage, except recombinants
        for s in list(seq_parents.keys()):
            temp_lin = s.split("_")[0]
            if lin == temp_lin:
                count_target_lin += 1                  
                lin_all_mutate =  extract_ref_mut(seq_parents[s],ref_genome,lin_all_mutate)
            
        fv75 = []
        for m in set(lin_all_mutate):
            if lin_all_mutate.count(m) >= (0.75*count_target_lin):
                fv75.append(m)
        Lineage_v[lin] = fv75 # feature mutations for each lineages

    # CovRecomb detection
    linA_list = list(Lineage_v.keys())
    feature_mutation = []
    for l in Lineage_v:
        for v in Lineage_v[l]:
            feature_mutation.append(v)

    feature_mutations = list(set(feature_mutation))
    mutaions_num = len(feature_mutations)

    # read sequences
    seq_samples = {}
    with open(child_fasta_file) as h:
        for s in h.readlines():
            if s[0] == ">":
                seq_id = s.strip().split(">")[1]
            else:
                seq_samples[seq_id] = str(s.strip())
            
    # mutation calling
    Strain_list_snp = list(seq_samples.keys())
    samples_variants_all = {}
    for s in Strain_list_snp:
        samples_variants_all[s] = get_snps(seq_samples[s], ref_genome)
        
    max_bk_num = 2
    len_UAB = 4
    recom_total_num = len(samples_variants_all)

    identidied_recom_info, time_microsecond1, time_second1, time_minute1, time_hour1 \
        = recombination_detection_test(starttime,max_bk_num, Strain_list_snp,len_UAB,linA_list,samples_variants_all,feature_mutations,Lineage_v,mutaions_num,recom_total_num)
    
    TPR1 = round(len(identidied_recom_info)/recom_total_num,4)
    covrecomb_results = [str(recom_total_num),str(TPR1), str(time_microsecond1), str(time_second1), str(time_minute1), str(time_hour1),str(cor_num)]
    print(covrecomb_results)
    with open(turns_path+"covrecomb/covrecomb_identified_results.csv","w+") as f:
        f.write(",".join(["recombinant","PA","PB"])+"\n")
        for epi in identidied_recom_info:
            f.write(epi+","+identidied_recom_info[epi][0]+","+identidied_recom_info[epi][1]+"\n")
    with open(turns_path+"methods_results_0605.csv","a+")as h:
        h.write("turns"+str(n+1)+","+"CovRecomb"+","+",".join(covrecomb_results)+"\n")
    
    print("CovRecomb Finished!")
        
    #### ----------------------------- rebar  -----------------------------
    rebarpath = "/home/jovyan/rebar/"
    os.chdir(rebarpath)
    turns_path = dirpath+"2_first_test/turns"+str(n+1)+"/"
    rebar_output = turns_path+"rebar/"

    for file in os.listdir(turns_path):
        if file.startswith("real_recom_lineage_samples_"):
            child_fasta_file = turns_path+file

    # read sequences
    seq_samples = {}
    with open(child_fasta_file) as h:
        for s in h.readlines():
            if s[0] == ">":
                seq_id = s.strip().split(">")[1]
            else:
                seq_samples[seq_id] = str(s.strip())

    recom_total_num = sample_size = len(seq_samples)

    recom_path = rebar_output+"real_recom_lineage_samples_rebar.fasta"
    with open(recom_path,"w+") as f:
        with open(child_fasta_file) as h:
            for s in h.readlines():
                if s[0] == ">":
                    seq_id = s.strip().replace(" ","_")
                    f.write(seq_id+"\n")
                else:
                    f.write(str(s.strip())+"\n")

    starttime = datetime.datetime.now()
    subprocess.call (["cd %s && \
        echo y | rebar run --dataset dataset/sars-cov-2-latest --alignment %s --output-all --outdir %s" % (rebarpath,recom_path,rebar_output)],shell=True)

    endtime = datetime.datetime.now()
    time_microsecond = (endtime -starttime).seconds * 1000 + (endtime -starttime).microseconds / 1000
    time_second, time_minute, time_hour = TimeConverter(time_microsecond)

    recom_identified = 0
    identidied_recom_info = {}
    df = pd.read_csv(rebar_output+"summary.tsv",sep = "\t")
    for i in df.index:
        epi = df.loc[i,"strain"]
        if df.loc[i,"clade"] == "recombinant":
            recom_identified+=1
            if type(df.loc[i,"parents_lineage"]) == str:
                PA = df.loc[i,"parents_lineage"].split(",")[0]
                PB = df.loc[i,"parents_lineage"].split(",")[1]
                identidied_recom_info[epi] = [PA,PB]
            else:
                identidied_recom_info[epi] = ["unknown","unknown"]

    TPR = round(recom_identified/recom_total_num,4)
    rebar_results = [str(recom_total_num),str(TPR), str(time_microsecond), str(time_second), str(time_minute), str(time_hour),str(cor_num)]
    print(rebar_results)
    
    with open(turns_path+"rebar/rebar_identified_results.csv","w+") as f:
        f.write(",".join(["recombinant","PA","PB"])+"\n")
        for epi in identidied_recom_info:
            f.write(epi+","+identidied_recom_info[epi][0]+","+identidied_recom_info[epi][1]+"\n")
            
    # Write results to output file
    with open(turns_path+"methods_results_0605.csv","a+")as h:
        h.write("turns"+str(n+1)+","+"rebar"+","+",".join(rebar_results)+"\n")

    print("rebar Finished!")
    #### ----------------------------- 3seq  -----------------------------
    turns_path = dirpath+"2_first_test/turns"+str(n+1)+"/"
    for file in os.listdir(turns_path):
        if file.startswith("real_parental_lineage_"):
            parent_fasta_file = turns_path+file
        elif file.startswith("real_recom_lineage_samples_"):
            child_fasta_file = turns_path+file

    ## read sequences
    import datetime
    starttime = datetime.datetime.now()
    SEQ3_outpath = turns_path+"seq3/"
    # creat_dir(SEQ3_outpath)

    seq_samples = {}
    with open(child_fasta_file) as h:
        for s in h.readlines():
            if s[0] == ">":
                seq_id = s.strip().split(">")[1]
            else:
                seq_samples[seq_id] = str(s.strip())

    recom_total_num = sample_size = len(seq_samples)

    subprocess.call (["cd /home/jovyan/work/0_method_tools/3seq_build/ && echo y | ./3seq -f %s %s -t1 -id %s" % (parent_fasta_file, child_fasta_file,SEQ3_outpath+"3SEQ_test")],shell=True)

    endtime = datetime.datetime.now()
    time_microsecond2 = (endtime -starttime).seconds * 1000 + (endtime -starttime).microseconds / 1000
    time_second2, time_minute2, time_hour2 = TimeConverter(time_microsecond2)

    seq3_true_pos = 0
    accurate_num = 0
    identidied_recom_info = {}
    for file in os.listdir(SEQ3_outpath):
        if file[-7:] == ".3s.rec":
            file_path = SEQ3_outpath+"/"+file
            with open(file_path,"r") as hseq:
                rows = hseq.readlines()
            if len(rows) == 1: # with no recombinant
                overall_correct_rate = 0
            else:
                seq3_true_pos = 0
                for row in range(1,len(rows)):
                    row_info  = rows[row].split("\t")
                    epi = rows[row].split("\t")[2]
                    pvalue = float(rows[row].split("\t")[9])
                    if pvalue < 0.05:
                        seq3_true_pos += 1
                        PA, PB = row_info[0].split("_")[0], row_info[1].split("_")[0]
                        identidied_recom_info[epi] = [PA,PB]

    TPR2 = round(seq3_true_pos/recom_total_num,4)
    SEQ3_results = [str(recom_total_num),str(TPR2), str(time_microsecond2), str(time_second2), str(time_minute2), str(time_hour2),str(cor_num)]
    print(SEQ3_results)
    
    with open(turns_path+"seq3/seq3_identified_results.csv","w+") as f:
        f.write(",".join(["recombinant","PA","PB"])+"\n")
        for epi in identidied_recom_info:
            f.write(epi+","+identidied_recom_info[epi][0]+","+identidied_recom_info[epi][1]+"\n")
            
    with open(turns_path+"methods_results_0605.csv","a+")as h:
        h.write("turns"+str(n+1)+","+"3SEQ"+","+",".join(SEQ3_results)+"\n")
    
    print("3seq Finished")
    
    turns_path = dirpath+"2_first_test/turns"+str(n+1)+"/"
    for file in os.listdir(turns_path):
        if file.startswith("real_parental_lineage_"):
            parent_fasta_file = turns_path+file
        elif file.startswith("real_recom_lineage_samples_"):
            child_fasta_file = turns_path+file

    virusrecom_output = turns_path+"virusrecom/"

    # read sequences
    seq_samples = {}
    with open(child_fasta_file) as h:
        for s in h.readlines():
            if s[0] == ">":
                seq_id = s.strip().split(">")[1]
            else:
                seq_samples[seq_id] = str(s.strip())
                
    recom_total_num = sample_size = len(seq_samples)

    with open(virusrecom_output+"reference_lineages_name.txt","w+") as f:
        for lin in all_need_parents:
            f.write(lin+"\n")

    num = 0
    for seq in seq_samples:
        num+=1
        with open(virusrecom_output+"seq"+str(num)+"/"+"recom_parent_seq"+str(num)+".fasta","w+") as h:
            h.write(">"+seq+"\n")
            h.write(seq_samples[seq]+"\n")
            with open(parent_fasta_file) as f:
                for j in f.readlines():
                    h.write(j)

    turns_path = dirpath+"2_first_test/turns"+str(n+1)+"/"
    for file in os.listdir(turns_path):
        if file.startswith("real_parental_lineage_"):
            parent_fasta_file = turns_path+file
        elif file.startswith("real_recom_lineage_samples_"):
            child_fasta_file = turns_path+file

    virusrecom_output = turns_path+"virusrecom/"

    # read sequences
    seq_samples = {}
    with open(child_fasta_file) as h:
        for s in h.readlines():
            if s[0] == ">":
                seq_id = s.strip().split(">")[1]
            else:
                seq_samples[seq_id] = str(s.strip())
                
    recom_total_num = sample_size = len(seq_samples)
    
    virus_recom_code_path = dirpath+"0_method_tools/virusrecom_v1.1_linux/recombination_test_data_v1.1/aligned_input_sequences/"

    starttime = datetime.datetime.now()
    viusrecom_identified = 0
    identidied_recom_info = {}
    for x in range(recom_total_num):
        viusrecom_identified, identidied_recom_info = virusrecom_analysis(x,viusrecom_identified, identidied_recom_info,virusrecom_output,virus_recom_code_path)

    endtime = datetime.datetime.now()
    time_microsecond3 = (endtime -starttime).seconds * 1000 + (endtime -starttime).microseconds / 1000
    time_second3, time_minute3, time_hour3 = TimeConverter(time_microsecond3)
        
    TPR3 = round(viusrecom_identified/recom_total_num,4)
    virusrecom_results = [str(recom_total_num),str(TPR3), str(time_microsecond3), str(time_second3), str(time_minute3), str(time_hour3),str(cor_num)]
    print(virusrecom_results)
    
    with open(turns_path+"virusrecom/virusrecom_identified_results.csv","w+") as f:
        f.write(",".join(["recombinant","PA","PB"])+"\n")
        for epi in identidied_recom_info:
            f.write(epi+","+identidied_recom_info[epi][0]+","+identidied_recom_info[epi][1]+"\n")

    # Write results to output file
    with open(turns_path+"methods_results_0605.csv","a+")as h:
        h.write("turns"+str(n+1)+","+"VirusRecom"+","+",".join(virusrecom_results)+"\n")

    print("VirusRecom Finished!")

['72', '0.3194', '12744.06', '12.74', '0.21', '0.0', '1']
CovRecomb Finished!
2023-06-05 11:54:55.531566	Using 1 CPUs out of 72 available.
2023-06-05 11:54:55.531744	----------------------------------------
2023-06-05 11:54:55.531802	BEGINNING SUBCOMMAND: run.
2023-06-05 11:54:55.531897	----------------------------------------
2023-06-05 11:54:55.531950	Parsing substitutions from alignment.
2023-06-05 11:54:55.531994	Importing reference: dataset/sars-cov-2-latest/reference.fasta
2023-06-05 11:54:55.540265	Importing alignment: /home/jovyan/work/2_first_test/turns2/rebar/real_recom_lineage_samples_rebar.fasta


2023-06-05 11:54:55.583569      Parsing substitutions from alignment: 100%|██████████| 72/72 [00:01<00:00, 52.34it/s]


2023-06-05 11:54:56.965045	Parsing substitutions benchmark: 0.01919 s/seq, 52.11972 seq/s
2023-06-05 11:54:56.965330	Exporting results to: /home/jovyan/work/2_first_test/turns2/rebar/subs.tsv
2023-06-05 11:54:57.238233	Finished parsing substitutions.
2023-06-05 11:54:57.240523	----------------------------------------
2023-06-05 11:54:57.240666	Detecting recombination.
2023-06-05 11:54:57.240823	Importing substitutions: /home/jovyan/work/2_first_test/turns2/rebar/subs.tsv
2023-06-05 11:54:57.247175	Importing dataset info: dataset/sars-cov-2-latest/dataset.yaml
2023-06-05 11:54:57.250639	Importing barcodes: dataset/sars-cov-2-latest/barcodes.tsv
2023-06-05 11:55:00.395856	Importing diagnostic barcodes: dataset/sars-cov-2-latest/diagnostic.tsv
2023-06-05 11:55:00.405162	Importing tree: dataset/sars-cov-2-latest/tree.nwk
2023-06-05 11:55:00.432684	Importing lineage to clade mapping: dataset/sars-cov-2-latest/lineage_to_clade.tsv


2023-06-05 11:55:00.507035      Detecting recombination: 100%|██████████| 72/72 [08:45<00:00,  7.30s/it]


2023-06-05 12:03:46.480164	Detecting recombination benchmark: 7.30518 s/seq, 0.13689 seq/s
2023-06-05 12:03:46.480477	Preparing to export.
2023-06-05 12:03:46.487041	Exporting YAML: /home/jovyan/work/2_first_test/turns2/rebar/summary.yaml
2023-06-05 12:03:47.596792	Exporting TSV: /home/jovyan/work/2_first_test/turns2/rebar/summary.tsv
2023-06-05 12:03:47.706649	Exporting barcode mutations: /home/jovyan/work/2_first_test/turns2/rebar/barcodes/<recombinant>_<parent_1>_<parent_2>.tsv
2023-06-05 12:03:50.412248	Exporting plots: /home/jovyan/work/2_first_test/turns2/rebar/plots/<recombinant>_<parent_1>_<parent_2>.png
Loaded backend module://matplotlib_inline.backend_inline version unknown.
2023-06-05 12:05:26.740098	Finished detecting recombination.
2023-06-05 12:05:26.770858	----------------------------------------
2023-06-05 12:05:26.771000	RUNTIME: 10.5 minutes
2023-06-05 12:05:26.771064	FINISHED SUBCOMMAND: run.
['72', '0.7917', '633790.088', '633.79', '10.56', '0.18', '1']
rebar Finish

...


-------------------------------------------------
  Name: Virus Recombination (VirusRecom)
  Description: Detecting recombination of viral lineages (or subtypes) using information theory.
  Version: 1.1 (2023-03-07)
  Author: Zhi-Jian Zhou
  Citation: Brief Bioinform. 2023 Jan 19;24(1)
-------------------------------------------------

Namespace(align_tool='', alignment='/home/jovyan/work/2_first_test/turns6/virusrecom/seq70/recom_parent_seq70.fasta', breakpoint='n', breakwin=200, cumulative='n', engrave='', export_name='', gap='n', input_wic='', legend='auto', lineages='/home/jovyan/work/2_first_test/turns6/virusrecom/reference_lineages_name.txt', max_region=1000, method='p', only_wic='n', outdir='/home/jovyan/work/2_first_test/turns6/virusrecom/seq70/', percentage=0.9, query='hCoV-19', step=20, thread=1, unalignment='', window=100, y_start=0.0)


>>> VirusRecom is importing sequence set, please wait patiently...

>>> VirusRecom is removing sites (columns) containing gap (-)...

>>> 

Fontconfig warning: line 5: unknown element "its:rules"
Fontconfig warning: line 6: unknown element "its:translateRule"
Fontconfig error: line 6: invalid attribute 'translate'
Fontconfig error: line 6: invalid attribute 'selector'
Fontconfig error: line 7: invalid attribute 'xmlns:its'
Fontconfig error: line 7: invalid attribute 'version'
Fontconfig warning: line 9: unknown element "description"
Fontconfig warning: "/etc/fonts/conf.d/10-hinting-slight.conf", line 4: unknown element "its:rules"
Fontconfig warning: "/etc/fonts/conf.d/10-hinting-slight.conf", line 5: unknown element "its:translateRule"
Fontconfig error: "/etc/fonts/conf.d/10-hinting-slight.conf", line 5: invalid attribute 'translate'
Fontconfig error: "/etc/fonts/conf.d/10-hinting-slight.conf", line 5: invalid attribute 'selector'
Fontconfig error: "/etc/fonts/conf.d/10-hinting-slight.conf", line 6: invalid attribute 'xmlns:its'
Fontconfig error: "/etc/fonts/conf.d/10-hinting-slight.conf", line 6: invalid attribute 'versi


-------------------------------------------------
  Name: Virus Recombination (VirusRecom)
  Description: Detecting recombination of viral lineages (or subtypes) using information theory.
  Version: 1.1 (2023-03-07)
  Author: Zhi-Jian Zhou
  Citation: Brief Bioinform. 2023 Jan 19;24(1)
-------------------------------------------------

Namespace(align_tool='', alignment='/home/jovyan/work/2_first_test/turns6/virusrecom/seq71/recom_parent_seq71.fasta', breakpoint='n', breakwin=200, cumulative='n', engrave='', export_name='', gap='n', input_wic='', legend='auto', lineages='/home/jovyan/work/2_first_test/turns6/virusrecom/reference_lineages_name.txt', max_region=1000, method='p', only_wic='n', outdir='/home/jovyan/work/2_first_test/turns6/virusrecom/seq71/', percentage=0.9, query='hCoV-19', step=20, thread=1, unalignment='', window=100, y_start=0.0)


>>> VirusRecom is importing sequence set, please wait patiently...

>>> VirusRecom is removing sites (columns) containing gap (-)...

>>> 

Fontconfig warning: line 5: unknown element "its:rules"
Fontconfig warning: line 6: unknown element "its:translateRule"
Fontconfig error: line 6: invalid attribute 'translate'
Fontconfig error: line 6: invalid attribute 'selector'
Fontconfig error: line 7: invalid attribute 'xmlns:its'
Fontconfig error: line 7: invalid attribute 'version'
Fontconfig warning: line 9: unknown element "description"
Fontconfig warning: "/etc/fonts/conf.d/10-hinting-slight.conf", line 4: unknown element "its:rules"
Fontconfig warning: "/etc/fonts/conf.d/10-hinting-slight.conf", line 5: unknown element "its:translateRule"
Fontconfig error: "/etc/fonts/conf.d/10-hinting-slight.conf", line 5: invalid attribute 'translate'
Fontconfig error: "/etc/fonts/conf.d/10-hinting-slight.conf", line 5: invalid attribute 'selector'
Fontconfig error: "/etc/fonts/conf.d/10-hinting-slight.conf", line 6: invalid attribute 'xmlns:its'
Fontconfig error: "/etc/fonts/conf.d/10-hinting-slight.conf", line 6: invalid attribute 'versi


-------------------------------------------------
  Name: Virus Recombination (VirusRecom)
  Description: Detecting recombination of viral lineages (or subtypes) using information theory.
  Version: 1.1 (2023-03-07)
  Author: Zhi-Jian Zhou
  Citation: Brief Bioinform. 2023 Jan 19;24(1)
-------------------------------------------------

Namespace(align_tool='', alignment='/home/jovyan/work/2_first_test/turns6/virusrecom/seq72/recom_parent_seq72.fasta', breakpoint='n', breakwin=200, cumulative='n', engrave='', export_name='', gap='n', input_wic='', legend='auto', lineages='/home/jovyan/work/2_first_test/turns6/virusrecom/reference_lineages_name.txt', max_region=1000, method='p', only_wic='n', outdir='/home/jovyan/work/2_first_test/turns6/virusrecom/seq72/', percentage=0.9, query='hCoV-19', step=20, thread=1, unalignment='', window=100, y_start=0.0)


>>> VirusRecom is importing sequence set, please wait patiently...

>>> VirusRecom is removing sites (columns) containing gap (-)...

>>> 

In [28]:
## calculate the accurate rate for each methods
def tihuan(CH):
    if CH == "B.1.617.2":
        return "AY."
    elif CH == "BF.5":
        return "BA.5.2"
    elif CH == "BJ.1":
        return "BA.2.10"
    elif CH == "BM.1.1.1": 
        return "BA.2.75"
    elif CH == "CJ.1":
        return "BA.2.75"
    elif CH == "CH.1.1.16":
        return "BA.2.75"
    elif CH == "BG.5":
        return "BA.2.12"
    elif CH == "DE.1":
        return "BA.5.1" 
    elif CH == "CH.1.1.16":
        return "BA.2.75" 
    elif CH == "BD.1":
        return "BA.1" 
    elif CH == "BF.3":
        return "BA.5.2" 
    else:
        return CH

methods = ["covrecomb","seq3","virusrecom"] #"bolotie","ripples", "rebar"
for n in [1,2,3,4,5]:
    turns_path = dirpath+"2_first_test/turns"+str(n+1)+"/"
    seq_samples = {}
    for file in os.listdir(turns_path):
        if file.startswith("real_parental_lineage_"):
            parent_fasta_file = turns_path+file
        elif file.startswith("real_recom_lineage_samples_"):
            child_fasta_file = turns_path+file

    with open(child_fasta_file) as h:
        for s in h.readlines():
            if s[0] == ">":
                seq_id = s.strip().split(">")[1]
            else:
                seq_samples[seq_id] = str(s.strip())

    recom_total_num = sample_size = len(seq_samples)
    parents
    epi_parents = {}
    for epi in seq_samples:
        CH1,CH2 = parents[pango_lineage[epi]][0], parents[pango_lineage[epi]][1]
        CH1,CH2 = tihuan(CH1),tihuan(CH2)
        epi_parents[epi] = [CH1,CH2]

    for method in methods:
        # method = "virusrecom"
        accurate_num = 0
        method_path = turns_path+method+"/"
        for file in os.listdir(method_path):
            if "_identified_results" in file:
                df = pd.read_csv(method_path+file)
                for i in df.index:
                    epi, PA, PB = df.loc[i,"recombinant"], df.loc[i,"PA"], df.loc[i,"PB"]
                    PA,PB = tihuan(PA),tihuan(PB)
                    CH1_r,CH2_r = tihuan(epi_parents[epi][0]),tihuan(epi_parents[epi][1])
                    # print("[",CH1_r,",", CH2_r,"]","       ", PA,"   ",PB)

                    if (set(CH2_r)-set(PA)== set() and set(CH1_r) - set(PB) == set()) or (set(CH2_r) - set(PB) == set() and  set(CH1_r) -set(PA)== set()) or \
                    (set(PA)-set(CH2_r)== set() and set(PB) - set(CH1_r) == set()) or (set(PB) - set(CH2_r) == set() and  set(PA) -set(CH1_r)== set()) :
                        accurate_num += 1
                    else:
                        continue

        accurate_rate = accurate_num/int(df.shape[0])
        print("turns",str(n+1),"   ",method,"  ", accurate_rate)
        
        with open(turns_path+"methods_accurate_0605.csv","a+")as h:
            h.write("turns"+str(n+1)+","+method+","+str(accurate_rate)+"\n")


turns 2     covrecomb    0.9565217391304348
turns 2     seq3    0.5857142857142857
turns 2     virusrecom    0.8
turns 3     covrecomb    1.0
turns 3     seq3    0.8780487804878049
turns 3     virusrecom    0.6341463414634146
turns 4     covrecomb    0.9642857142857143
turns 4     seq3    0.16176470588235295
turns 4     virusrecom    0.7027027027027027
turns 5     covrecomb    1.0
turns 5     seq3    0.9210526315789473
turns 5     virusrecom    0.7407407407407407
turns 6     covrecomb    1.0
turns 6     seq3    0.875
turns 6     virusrecom    0.5416666666666666


In [29]:
## calculate the accurate rate for each methods
methods = ["rebar"] #"bolotie","ripples"
for n in [1,2,3,4,5]:
    turns_path = dirpath+"2_first_test/turns"+str(n+1)+"/"
    seq_samples = {}
    for file in os.listdir(turns_path):
        if file.startswith("real_parental_lineage_"):
            parent_fasta_file = turns_path+file
        elif file.startswith("real_recom_lineage_samples_"):
            child_fasta_file = turns_path+file

    with open(child_fasta_file) as h:
        for s in h.readlines():
            if s[0] == ">":
                seq_id = s.strip().split(">")[1]
            else:
                seq_samples[seq_id] = str(s.strip())

    recom_total_num = sample_size = len(seq_samples)
    epi_parents = {}
    for epi in seq_samples:
        CH1,CH2 = parents[pango_lineage[epi]][0], parents[pango_lineage[epi]][1]
        CH1,CH2 = tihuan(CH1),tihuan(CH2)
        epi0 = epi.replace(" ","_")
        epi_parents[epi0] = [CH1,CH2]

        
    method = "rebar"
    accurate_num = 0
    method_path = turns_path+method+"/"
    for file in os.listdir(method_path):
        if "_identified_results" in file:
            df = pd.read_csv(method_path+file)
            for i in df.index:
                epi, PA, PB = df.loc[i,"recombinant"], df.loc[i,"PA"], df.loc[i,"PB"]
                PA,PB = tihuan(PA),tihuan(PB)
                CH1_r,CH2_r = tihuan(epi_parents[epi][0]),tihuan(epi_parents[epi][1])
                # print("[",CH1_r,",", CH2_r,"]","       ", PA,"   ",PB)

                if (set(CH2_r)-set(PA)== set() and set(CH1_r) - set(PB) == set()) or (set(CH2_r) - set(PB) == set() and  set(CH1_r) -set(PA)== set()) or \
                (set(PA)-set(CH2_r)== set() and set(PB) - set(CH1_r) == set()) or (set(PB) - set(CH2_r) == set() and  set(PA) -set(CH1_r)== set()) :
                    accurate_num += 1
                else:
                    continue


    accurate_rate = accurate_num/int(df.shape[0])
    print("turns",str(n+1),"   ",method,"  ", accurate_rate)

    with open(turns_path+"methods_accurate_0605.csv","a+")as h:
        h.write("turns"+str(n+1)+","+method+","+str(accurate_rate)+"\n")


turns 2     rebar    0.8245614035087719
turns 3     rebar    0.7777777777777778
turns 4     rebar    0.7857142857142857
turns 5     rebar    0.7678571428571429
turns 6     rebar    0.7636363636363637


In [ ]:
## Ripples
# nohup python3 ./RIPPLES_run.py > RIPPLES_run.log 2>&1 &